# Validation of CSAD Simulation Model

Based on the experiments conducted in the MC Lab fall 2022 with Raphael Mounet, we want to compare the response observed in the experiments with those simulated in our simulation model. We can use the same wave realization as used in the MC Lab. However, the experiments used a wave realization with 500 wave components. This will take some time to simulate with our model as the 2nd order waveloads will on average need 0.05 seconds to calculate, which is 5 times higher than the simulation time step $dt = 0.01$. We will first test with 100 wave components, and compare the results. If time, the number of wave components will be increased. 

### Procedure

The "validation" process will consist of the following steps:


1.  Get the wave realization used in the experiments. This includes obtaining the individual wave components. 
2.  Use cross spectral density method from scipy.signal to plot the wave spectra of the wave realizations.
3.  Get the heave and pitch response of CSAD from experiments
4.  CSD to calculate response spectra in the different sea states.
5.  Run CSAD simulation model in the same sea states - with the same wave components - as in experiments.
6.  Compute CSD (PSD) for heave and pitch response of CSAD Simulation model.
7.  Compare experimental and simulated response spectra. 



In [1]:
# Import necessary modules 
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

# Set plot parameters
width = 426.8       # Latex document width in pts
inch_pr_pt = 1/72.27        # Ratio between pts and inches

golden_ratio = (np.sqrt(5) - 1)/2
fig_width = width*inch_pr_pt
fig_height = fig_width*golden_ratio
fig_size = [fig_width, fig_height]

params = {'backend': 'PS',
          'axes.labelsize': 10,
          'font.size': 10,
          'legend.fontsize': 10,
          'xtick.labelsize': 8,
          'ytick.labelsize': 8,
          'text.usetex': True,
          'figure.figsize': fig_size} 

plt.rcParams.update(params)

from apread import APReader

from scipy.signal import csd

import os

basedir = os.getcwd()
print(basedir)

c:\Users\j-ehy\OneDrive - NTNU\NTNU\9 semester\ProsjektOppgave\wavemodel\Wave-Model\notebooks


### 1. Get Experiment Wave Realizations

In [2]:
# Folder to experimental results.
datadir = os.path.abspath(os.path.join(basedir, '../../..', 'mclab', 'Experiments_MCLab_Fall22'))
sea_state_dir = os.path.join(datadir, 'Wave_Input', 'SeaStates_for_models')
seed_specs_dir = os.path.join(sea_state_dir, 'Seed_specs')
csad_data_dir = os.path.join(datadir, 'MCL_CSAD_testresults')
result_files = [os.path.join(csad_data_dir, file) for file in os.listdir(csad_data_dir) if file.endswith('.BIN')]
sea_state_files = [os.path.join(sea_state_dir, file) for file in os.listdir(sea_state_dir) if file.endswith('.csv')][1:]

print(f"Result files = {os.listdir(csad_data_dir)}")

sea_states_used = [int(file.split('_')[0][2:]) for file in os.listdir(csad_data_dir) if file.endswith('.BIN')]
sea_state_params = {
    1: (0.03, 0.7, 3.3),
    2: (0.04, 0.8, 3.3),
    3: (0.04, 0.9, 1.8),
    4: (0.05, 1.0, 1.8),
    5: (0.05, 1.1, 1.0),
    6: (0.06, 1.2, 1.0),
    7: (0.06, 1.3, 1.0),
    8: (0.06, 1.4, 1.0),
    9: (0.06, 1.5, 1.0),
    10: (0.03, 1.5, 1.0)
}
wave_realizations = {int(sea_state_files[i].split('\\')[-1].split('_')[0].split('SeaState')[-1]): np.genfromtxt(sea_state_files[i], delimiter=",")[1:, 1:3] for i in range(len(sea_state_files))}
print(f"Sea states used: {sea_states_used}")

csad_results = {sea_states_used[i]: APReader(result_files[i]) for i in range(len(result_files))}

Result files = ['SS10_Real1_CSAD-1.BIN', 'SS10_Real1_CSAD-1.TST', 'SS1_Real1_CSAD-1.BIN', 'SS1_Real1_CSAD-1.TST', 'SS1_Real1_CSAD-2.BIN', 'SS1_Real1_CSAD-2.TST', 'SS4_Real1_CSAD-1.BIN', 'SS4_Real1_CSAD-1.TST', 'SS7_Real1_CSAD-1.BIN', 'SS7_Real1_CSAD-1.TST', 'SS9_Real1_CSAD-1.BIN', 'SS9_Real1_CSAD-1.TST', 'SS9_Real1_CSAD-2.BIN', 'SS9_Real1_CSAD-2.TST']
Sea states used: [10, 1, 1, 4, 7, 9, 9]


In [3]:
print(os.listdir(seed_specs_dir))

# Select sea state
sea_state = 9
_sparsity = 1   # Select the step size for choosing number of wave components (5 = 100 wave components, 2 = 250 wave components, 1 = 500)
plot_result_dir = os.path.join(os.getcwd(), f"Sea_state_{sea_state}")
plot_result_dir = f"Sea_state_{sea_state}"

# Get one of the sea_states
with open(os.path.join(seed_specs_dir, os.listdir(seed_specs_dir)[sea_state-1]), 'r') as f:
    df = pd.read_csv(f)

wave_amps = df['wave_amp [m]'].to_numpy()[::_sparsity]
wave_freqs = df['freq. [Hz]'].to_numpy()[::_sparsity]*2*np.pi
epsilon = df['epsilon [rad]'].to_numpy()[::_sparsity]
wave_angles = np.ones_like(wave_amps)*np.pi     # To make unidirectional head sea waves.

def jonswap(w, hs, tp, gamma):
    wp = 2*np.pi / tp
    w = np.asarray(w)
    sigma = np.empty_like(w)
    arg = w <= wp
    sigma[arg] = 0.07
    sigma[~arg] = 0.09

    r = np.exp(-0.5*((w - wp)/(sigma*wp))**2)
    alpha = 1 - 0.287*np.log(gamma)
    A = 5.0/16.0 * hs**2 * wp**4
    B = 5.0/4.0 * wp**4
    return alpha*A/w**5 * np.exp(-B/w**4)*gamma**r




['SS1_Real1_seed1_seedspecs.csv', 'SS2_Real1_seed1_seedspecs.csv', 'SS3_Real1_seed1_seedspecs.csv', 'SS4_Real1_seed1_seedspecs.csv', 'SS5_Real1_seed1_seedspecs.csv', 'SS6_Real1_seed1_seedspecs.csv', 'SS7_Real1_seed1_seedspecs.csv', 'SS8_Real1_seed1_seedspecs.csv', 'SS9_Real1_seed1_seedspecs.csv']


### 2. Plot Experiment Wave Spectra

In [4]:
sampling_freq = 1/np.mean(csad_results[sea_state].Channels[0].data[1:] - csad_results[sea_state].Channels[0].data[0:-1])

time = wave_realizations[sea_state][:, 0]
fs = 1/np.mean(time[1:] - time[0:-1])
print(fs)
wave_elevation = wave_realizations[sea_state][:, 1]

wf, wave_psd = csd(wave_elevation, wave_elevation, fs=fs, nperseg=2**11)
f_max = 5       # Max freq [Hz]
plt.figure(figsize=(12, 6))
plt.plot(wf[wf < f_max], wave_psd[wf < f_max], label="$S_w(\omega)$")
plt.plot(wf[wf < f_max], jonswap(wf[wf < f_max]*2*np.pi, *sea_state_params[sea_state])*2*np.pi, label="JONSWAP")
plt.legend()
plt.xlabel("$f \; [Hz]$")
plt.ylabel("Power Spectral Density")
plt.savefig(f"sea_state_{sea_state}.eps")
plt.show()

99.99943391046162


C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\1274510148.py:30: RuntimeWarning: divide by zero encountered in divide
  return alpha*A/w**5 * np.exp(-B/w**4)*gamma**r
C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\1274510148.py:30: RuntimeWarning: invalid value encountered in multiply
  return alpha*A/w**5 * np.exp(-B/w**4)*gamma**r
The PostScript backend does not support transparency; partially transparent artists will be rendered opaque.
C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\1419878928.py:17: UserWarning: Matplotlib is currently using ps, which is a non-GUI backend, so cannot show the figure.
  plt.show()


### 3. Get Experiment Repsonse Data

In [5]:
heave_response = csad_results[sea_state].Channels[3].data
pitch_response = csad_results[sea_state].Channels[5].data

heave = heave_response - np.mean(heave_response)
pitch = pitch_response - np.mean(pitch_response)

### 4. Experiment Response Spectra

In [6]:
sampling_freq = 1/np.mean(csad_results[sea_state].Channels[0].data[1:] - csad_results[sea_state].Channels[0].data[0:-1])
# Compute heave response spectra, only for the times where we have head sea!
t = csad_results[sea_state].Channels[0].data
t_max = np.max(t)
condition = (t > 1/11*t_max) & (t < 3/11*t_max)

plt.figure()
plt.title(f"Heave Response, {1/11*t_max:.2f} [s] $\leq$ t $\leq$ {3/11*t_max:.2f} [s]")
plt.plot(t[condition], heave[condition])
plt.xlim(t[condition][0], t[condition][-1])
plt.ylabel("$\eta_3$")
plt.xlabel("$t \; [s]$")
plt.show()

freqs, psd = csd(heave[condition], heave[condition], fs=sampling_freq, nperseg=2**11)
f_pitch, psd_pitch = csd(pitch[condition], pitch[condition], fs=sampling_freq, nperseg=2**11)
f_max = 5
plt.plot(freqs[freqs < f_max], psd[freqs < f_max])
plt.show()

plt.plot(freqs[freqs < f_max], psd[freqs < f_max])
plt.show()

C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\1039452946.py:13: UserWarning: Matplotlib is currently using ps, which is a non-GUI backend, so cannot show the figure.
  plt.show()
c:\Users\j-ehy\OneDrive - NTNU\NTNU\9 semester\ProsjektOppgave\wavemodel\wavesim\lib\site-packages\matplotlib\cbook\__init__.py:1369: ComplexWarning: Casting complex values to real discards the imaginary part
  return np.asarray(x, float)
C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\1039452946.py:19: UserWarning: Matplotlib is currently using ps, which is a non-GUI backend, so cannot show the figure.
  plt.show()
C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\1039452946.py:22: UserWarning: Matplotlib is currently using ps, which is a non-GUI backend, so cannot show the figure.
  plt.show()


### 5. Run CSAD Simulation

In [7]:
# Import csad simulator model and wave load module
from simulator.csad import CSAD_DP_6DOF
from waves.wave_loads import WaveLoad

from utils import Rzyx

# Simulation timestep
tmax = t[condition][-1]
dt = 0.01
sim_time = np.arange(t[condition][0], tmax, dt) # CHANGE START OF SIMULATION TO t[condition][0]!


csad = CSAD_DP_6DOF(dt)

# Try to change the damping and added mass of the simulator to check if we get a better comparison?
waveload = WaveLoad(wave_amps, wave_freqs, epsilon, wave_angles, config_file=csad._config_file)

# Define a simple controller for stationkeeping
Kp = np.diag([0.6, .6, .5])
Kd = np.diag([2, 2, 2])
def PD(eta, nu):
    R = Rzyx(eta)
    z1 = R.T@eta[[0, 1, 5]]
    z2 = nu[[0, 1, 5]]
    return -Kp@z1 - Kd@z2

heave_sim = np.zeros_like(sim_time)
x = np.zeros((len(sim_time), 12))
for i in range(1, len(sim_time)):
    print(f"t= {sim_time[i]:2f}")
    relative_angle = csad.get_eta()[-1] - wave_angles[0]
    tau_wf_1 = waveload.first_order_loads(sim_time[i], relative_angle, csad.get_eta())
    tau_wf_2 = waveload.second_order_loads(sim_time[i], relative_angle)
    tau_pd = PD(csad.get_eta(), csad.get_nu())
    tau_cmd = np.array([tau_pd[0], tau_pd[1], 0, 0, 0, tau_pd[2]])
    heave_sim[i] = csad.get_eta()[2]
    x[i] = csad._x
    csad.x_dot(0, 0, tau_wf_1 + tau_wf_2 + tau_cmd)
    csad.integrate()

np.savetxt(f'sim_results_x_seaState{sea_state}_N{len(wave_amps)}', x)
np.savetxt(f'sim_heave_{sea_state}_N{len(wave_amps)}', heave_sim)

500
Execution time of _full_qtf_6dof: 0.9286
t= 349.430017
Execution time of second_order_loads: 0.0578
t= 349.440017
Execution time of second_order_loads: 0.0571
t= 349.450017
Execution time of second_order_loads: 0.0422
t= 349.460017
Execution time of second_order_loads: 0.0587
t= 349.470017
Execution time of second_order_loads: 0.0544
t= 349.480017
Execution time of second_order_loads: 0.0574
t= 349.490017
Execution time of second_order_loads: 0.0573
t= 349.500017
Execution time of second_order_loads: 0.0590
t= 349.510017
Execution time of second_order_loads: 0.0492
t= 349.520017
Execution time of second_order_loads: 0.0449
t= 349.530017
Execution time of second_order_loads: 0.0401
t= 349.540017
Execution time of second_order_loads: 0.0468
t= 349.550017
Execution time of second_order_loads: 0.0542
t= 349.560017
Execution time of second_order_loads: 0.0492
t= 349.570017
Execution time of second_order_loads: 0.0480
t= 349.580017
Execution time of second_order_loads: 0.0448
t= 349.5900

### 6. Simulation Response Spectra

In [26]:
sim_freq, sim_psd = csd(heave_sim, heave_sim, fs=1/dt, nperseg=2**11)
sim_p_freq, sim_pitch_psd = csd(x[:, 4], x[:, 4], fs=1/dt, nperseg=2**11)
f_pitch, pitch_psd = csd(np.deg2rad(pitch[condition]), np.deg2rad(pitch[condition]), fs=sampling_freq, nperseg=2**11)

f_max = 2
#plt.figure(figsize=(12, 5))
plt.title(f"Heave Response | Sea state: {sea_state}, hs={sea_state_params[sea_state][0]}, tp={sea_state_params[sea_state][1]}")
plt.plot(sim_freq[sim_freq < f_max], sim_psd[sim_freq < f_max], label="Simulation")
plt.plot(freqs[freqs < f_max], psd[freqs < f_max], label="Experimental")
plt.xlabel("$f \; [hz]$")
plt.ylabel("$S(f)$")
plt.legend()
plt.savefig(f'sr_heave_sea_state{sea_state}_sp{_sparsity}.eps')
#plt.show()


#plt.figure(figsize=(12, 5))
plt.title(f"Pitch Repsonse | Sea state: {sea_state}, hs={sea_state_params[sea_state][0]}, tp={sea_state_params[sea_state][1]}")
plt.plot(sim_p_freq[sim_p_freq < f_max], sim_pitch_psd[sim_freq < f_max], label="Simulation")
plt.plot(f_pitch[f_pitch < f_max], pitch_psd[f_pitch < f_max], label="Experimental")
plt.xlabel("$f \; [hz]$")
plt.ylabel("$S(f)$")
plt.legend()
plt.savefig(f'sr_pitch_sea_state{sea_state}_sp{_sparsity}.eps')
#plt.show()


#plt.figure(figsize=(12, 6))
#plt.plot(wf[wf < f_max], wave_psd[wf < f_max], label="$S_w(f)$")
#plt.plot(wf[wf < f_max], jonswap(wf[wf < f_max]*2*np.pi, *sea_state_params[sea_state])*2*np.pi, label="JONSWAP")
#plt.legend()
#plt.xlabel("$f \; [Hz]$")
#plt.ylabel("Power Spectral Density")
#plt.show()

c:\Users\j-ehy\OneDrive - NTNU\NTNU\9 semester\ProsjektOppgave\wavemodel\wavesim\lib\site-packages\matplotlib\cbook\__init__.py:1369: ComplexWarning: Casting complex values to real discards the imaginary part
  return np.asarray(x, float)
The PostScript backend does not support transparency; partially transparent artists will be rendered opaque.
c:\Users\j-ehy\OneDrive - NTNU\NTNU\9 semester\ProsjektOppgave\wavemodel\wavesim\lib\site-packages\matplotlib\cbook\__init__.py:1369: ComplexWarning: Casting complex values to real discards the imaginary part
  return np.asarray(x, float)
The PostScript backend does not support transparency; partially transparent artists will be rendered opaque.


In [27]:
# plt.figure(figsize=(10, 10))
# plt.plot(x[:, 1], x[:, 0])
# plt.xlabel("E")
# plt.ylabel("N")
# plt.xlim(-1, 1)
# plt.ylim(-1, 1)
# plt.show()

# plt.figure(figsize=(16, 4))
# plt.plot(sim_time, np.rad2deg(x[:, 5]), label="$\psi$")
# plt.legend()
# plt.show()

# plt.figure(figsize=(16, 4))
# plt.plot(t[condition], heave[condition]-np.mean(heave[condition]), label="Experiment")
# plt.plot(sim_time, x[:, 2], label=r"$\eta_3$ Sim")
# plt.legend()
# plt.show()

# plt.figure(figsize=(16, 4))
# plt.plot(sim_time, x[:, 6], label="$u$")
# plt.plot(sim_time, x[:, 7], label="$v$")
# plt.legend()
# plt.show()

# plt.figure(figsize=(16, 4))
# plt.plot(sim_time, np.rad2deg(x[:, 4]), label=r"$\theta$")
# plt.plot(t[condition], pitch[condition] - np.mean(pitch[condition]))
# plt.show()

### 7. Response Spectra Comparison

In [36]:
# Calculate and compare response spectra in each DOF for experimental and simulation
from matplotlib.ticker import StrMethodFormatter

fig, ax = plt.subplots(3, 2, constrained_layout=True)#, figsize=(16, 24))
fig.suptitle("Response Spectra | Sea state: {} | $H_s$={} [m], $T_p$={} [s], $\gamma$={} [-]".format(sea_state, *sea_state_params[sea_state]))
titles = ['Surge', 'Sway', 'Heave', 'Roll', 'Pitch', 'Yaw']

for i in range(6):
    #plt.sca(ax[i//3, i - 3*(i//3)])
    plt.sca(ax[i - 3*(i//3), i//3])
    plt.gca().yaxis.set_major_formatter(StrMethodFormatter('{x:.1f}'))
    plt.title(titles[i])
    f_sim, psd_dof = csd(x[:, i], x[:, i], fs=1/dt, nperseg=2**11)
    # Get experimental data
    timeseries = csad_results[sea_state].Channels[i+1].data
    # Remove mean offset
    timeseries_fixed = timeseries - np.mean(timeseries)
    
    if i > 2:
        # Convert to radians for dofs 4, 5, 6
        timeseries_fixed = np.deg2rad(timeseries_fixed)
    f_exp, psd_dof_exp = csd(timeseries_fixed[condition], timeseries_fixed[condition], fs=sampling_freq, nperseg=2**11)
    plt.plot(f_sim[f_sim < f_max], psd_dof[f_sim < f_max], label="Simulation")
    plt.plot(f_exp[f_exp < f_max], psd_dof_exp[f_exp < f_max], label="Experimental")
    #plt.legend()
    plt.xlabel("$f \; [hz]$")

plt.savefig(f'response_spectrum_all_dof_seastate{sea_state}_sp{_sparsity}.eps')
plt.show()

c:\Users\j-ehy\OneDrive - NTNU\NTNU\9 semester\ProsjektOppgave\wavemodel\wavesim\lib\site-packages\matplotlib\cbook\__init__.py:1369: ComplexWarning: Casting complex values to real discards the imaginary part
  return np.asarray(x, float)
C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\2655467077.py:29: UserWarning: Matplotlib is currently using ps, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [11]:
plt.plot(t[condition], (csad_results[sea_state].Channels[4].data)[condition])
plt.plot(sim_time, np.rad2deg(x[:, 3]))
plt.show()

plt.plot(t[condition], (csad_results[sea_state].Channels[5].data)[condition])
plt.plot(sim_time, np.rad2deg(x[:, 4]))
plt.show()


plt.plot(t[condition], (csad_results[sea_state].Channels[6].data)[condition])
plt.plot(sim_time, np.rad2deg(x[:, 5]))
plt.show()

C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\4140963576.py:3: UserWarning: Matplotlib is currently using ps, which is a non-GUI backend, so cannot show the figure.
  plt.show()
C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\4140963576.py:7: UserWarning: Matplotlib is currently using ps, which is a non-GUI backend, so cannot show the figure.
  plt.show()
C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\4140963576.py:12: UserWarning: Matplotlib is currently using ps, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [12]:
res = csad_results[sea_state].Channels[3].data[condition] - np.mean(csad_results[sea_state].Channels[3].data[condition])
ff, ppsd = csd(res, res, fs=sampling_freq, nperseg=2**11)
plt.plot(ff[ff < f_max], ppsd[ff < f_max])
plt.show()

C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\174861787.py:4: UserWarning: Matplotlib is currently using ps, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [13]:
csad_results[sea_state].fileName

'SS9_Real1_CSAD-2'

In [14]:
rao = np.asarray(waveload._params['motionRAO']['amp'])[:,:, :, 0]
rao_freq = np.asarray(waveload._params['motionRAO']['w'])
rao.shape

(6, 47, 36)

In [15]:
plt.plot(rao_freq/(2*np.pi), rao[2, :, 0])
plt.show()

C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\4050684080.py:2: UserWarning: Matplotlib is currently using ps, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [16]:
# Expected S_R for heave in the sea state - calculated by the RAO for CSAD and the wave spectra:

RAO = np.interp(wf*2*np.pi, rao_freq, rao[2, :, 0])
wave_psd_rad = np.abs(RAO)**2*wave_psd/(2*np.pi)


plt.plot(wf[wf < f_max], wave_psd_rad[wf < f_max]*2*np.pi)
plt.plot(ff[ff < f_max], ppsd[ff < f_max])
plt.show()

C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\291483024.py:9: UserWarning: Matplotlib is currently using ps, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [17]:
plt.plot((wf*2*np.pi)[wf < f_max], np.interp(wf*2*np.pi, rao_freq, rao[2, :, 0])[wf < f_max])
plt.show()

C:\Users\j-ehy\AppData\Local\Temp\ipykernel_11636\1509193825.py:2: UserWarning: Matplotlib is currently using ps, which is a non-GUI backend, so cannot show the figure.
  plt.show()


In [18]:
2*np.pi/sea_state_params[sea_state][1]

4.1887902047863905

In [19]:
wp = 2*np.pi/sea_state_params[sea_state][1]
Awp = np.interp(wp, np.array(waveload._params['freqs']), np.array(waveload._params['A'])[2, 2, :])
Bwp = np.interp(wp, np.array(waveload._params['freqs']), np.array(waveload._params['B'])[2, 2, :])
print(Awp)
print(Bwp)

191.5166204384424
713.7105122778717


In [20]:
print(csad._Ma[2, :])
print(csad._D[2, :])

[  0.        0.      193.32214   0.       24.88125   0.     ]
[  0.         0.       719.08606    0.        91.562698   0.      ]


In [21]:
wp/(2*np.pi)

0.6666666666666666